In [1]:
import pandas as pd
import numpy as np
import time
import random

# -*- coding: utf-8 -*-
from bs4 import BeautifulSoup
import requests
import re
from datetime import date
# remember to install the library: pip install scraperapi-sdk
from scraper_api import ScraperAPIClient

# for parallelization
from joblib import Parallel, delayed
import multiprocessing
from multiprocessing import Manager

headers = {'User-Agent':'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.183',#Safari/537.36
'Accept-Encoding': 'identity'
}


#'Accept-Encoding': 'identity'
#url = 'https://www.realtor.com/realestateandhomes-search/Atlanta_GA/pg-0'
#response=requests.get(url,headers=headers)

In [2]:
client = ScraperAPIClient('c72673098a63fab1bc69b67253f7c93b') #my gmail
#client = ScraperAPIClient('a27221db7e9a27526f076a1fdc66dc51') #hotmail
#county_lst = ["Cook-County_IL"]#,"DeKalb-County_GA","Fulton-County_GA", "Cobb-County_GA", "Gwinnett-County_GA", "Henry-County_GA", "Douglas-County_GA"]
city_lst = ["Chicago_IL"]

## Scraping Rentals

In [3]:
# this will be the new code. Needs validation that the listing coming out are cohesive. 
# It may make sense to add the listing link to the df so that can easily do a sanity check on the listing info

# also note that I realize using regex is janky. chatgpt wanted to use json to parse the listing info,
# but it seems the structure was so bad that json.loads never worked.

idx=0
prop_df = pd.DataFrame()
listings = []
#for county in county_lst:
for city in city_lst:
    
    """ Need to find out how many pages of results came back for each county search so can know how many to loop
    through. Find this info on the first page of results"""
    
    #url = 'https://www.realtor.com/apartments/' + county +'/pg-'
    url = 'https://www.realtor.com/apartments/' + city +'/pg-'
    
    realtor_url1 = url + str(0)
    
    #using scraper api instead of requests library
    response = client.get(url = realtor_url1)
    print(city)
    print(response)

    myr2 = response.text
    
    #this bit will work for getting listings count for apartments
    lstings_a = re.search('See all (.+apartments)', myr2)
    lstings_a = int(lstings_a.group(1).split(" ")[0].strip())
 
    ##couldn't find number of pages on the apartments search. So get the number of listings and assume 41 listings 
    #per page in order to figure out how many pages to loop through
    pages_of_results = round(lstings_a / 41)
    #pages_of_results = 2
    
    n_pages = 0
    
    for page in list(range(0, pages_of_results)):

        """Use the scaperapiclient to get requests from webpages using a different proxy for each page.
        Convert the content to soup, isolate the chunk of html we need and convert to string.
        Pull the info we need for each property from the string and put it into a list of dictionaries. 
        then can convert to dataframe
        .group() returns the part of the string where there was a match
        """
        print('page: ' + str(page))
        n_pages += 1
        realtor_url = url + "0" + str(page)
        print(realtor_url)

        response = client.get(url = realtor_url)
        print(response )

        #response=requests.get(realtor_url,headers=headers)

        soup = BeautifulSoup(response.content,'html.parser')

        #get the chunk of html that contains th info we want
        #and convert it to a string
        json_data = str(soup.find_all(id='__NEXT_DATA__')).split("props")[1]
        json_data = '{"props' + json_data

        #print(json_data)
        print("************************************")
        
        #This will give us the chunk of text with some of the listings info, to pull all the listing on a page
        r3 = json_data

        #get the indexes for property id and permalink so can know where to break up string for individual properties
        start_idx = [idx.start() for idx in re.finditer('property_id', r3)]
        end_idx = [idx.start() for idx in re.finditer('products":', r3)]

        
        for i in range(0, len(start_idx)-1):
            try:

                #loop through the text of html on a page and pull out the slices that correspond to a particular property.
                # don't use the end index, it throws everything off. Also search will just find the first match so it's fine.
                # search returns a match object
                r4 = r3[start_idx[i] : ]#end_idx[i]]

                listing_id = re.search('listing_id":(.+?),', r4)
                property_id = re.search('property_id":(.+?),', r4)
                prop_type = re.search('prop_type":(.+?),', r4)
                lat= re.search('lat":(.+?),', r4)    
                lon = re.search('lon":(.+?)}', r4)    
                address = re.search('line":(.+?),', r4)
                price = re.search('list_price":(.+?),', r4)
                price_max = re.search('list_price_max":(.+?),', r4)
                price_min = re.search('list_price_min":(.+?),', r4)
                permalink = re.search('permalink":(.+?),', r4)
                description = re.search('"description":(.*?)}', r4)
                """
                print(listing_id)
                print(address)
                print(price_max)
                print(permalink)
                print(description)
                """

                # create a list of dictionaries to store the info

                dic = {'property_id': property_id.group(1).replace('"',''),
                        'listing_id' : listing_id.group(1).replace('"',''), 
                        'prop_type' : prop_type.group(1).replace('"',''), 
                        'latitude': lat.group(1), 
                        'longitude': lon.group(1), 
                        'address': address.group(1).replace('"',''),
                        'price': price.group(1).replace('"',''),
                        'price_max' : price_max.group(1).replace('"',''),
                        'price_min' : price_max.group(1).replace('"',''),
                        'link' : 'https://www.realtor.com/realestateandhomes-detail/' + permalink.group(1).replace('"',''),
                        'description' : description.group(1).replace('"',' '),
                       }
                print(dic)
                print("********************")
                listings.append(dic)

            except:
                print("some exception for ", i)
                print("********************")


Chicago_IL
<Response [200]>
page: 0
https://www.realtor.com/apartments/Chicago_IL/pg-00
<Response [200]>
************************************
{'property_id': '8229072978', 'listing_id': '2949506156', 'prop_type': '[{type:home', 'latitude': '41.755477', 'longitude': '-87.555892', 'address': '2817 E 77TH ST', 'price': 'null', 'price_max': '870', 'price_min': '870', 'link': 'https://www.realtor.com/realestateandhomes-detail/2817-E-77th-St_Chicago_IL_60649_M82290-72978', 'description': '{ beds :null, beds_max :4, beds_min :0, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :1500, sqft_min :205, name : 2817 E 77th , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7502759759', 'listing_id': '2949506054', 'prop_type': '[{type:home', 'latitude': '41.768031', 'longitude': '-87.61751', 'address': '6954 S CALUMET AVE', 'price': 'null', 'price_max': '1110', 'price_min': '1110', 

<Response [200]>
************************************
{'property_id': '8229072978', 'listing_id': '2949506156', 'prop_type': '[{type:home', 'latitude': '41.755477', 'longitude': '-87.555892', 'address': '2817 E 77TH ST', 'price': 'null', 'price_max': '870', 'price_min': '870', 'link': 'https://www.realtor.com/realestateandhomes-detail/2817-E-77th-St_Chicago_IL_60649_M82290-72978', 'description': '{ beds :null, beds_max :4, beds_min :0, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :1500, sqft_min :205, name : 2817 E 77th , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7502759759', 'listing_id': '2949506054', 'prop_type': '[{type:home', 'latitude': '41.768031', 'longitude': '-87.61751', 'address': '6954 S CALUMET AVE', 'price': 'null', 'price_max': '1110', 'price_min': '1110', 'link': 'https://www.realtor.com/realestateandhomes-detail/6954-S-Calumet-Ave_Chicago_IL

<Response [200]>
************************************
{'property_id': '8270571155', 'listing_id': '2949506068', 'prop_type': '[{type:home', 'latitude': '41.756649', 'longitude': '-87.563039', 'address': '7612 S KINGSTON AVE', 'price': 'null', 'price_max': '915', 'price_min': '915', 'link': 'https://www.realtor.com/realestateandhomes-detail/7612-S-Kingston-Ave_Chicago_IL_60649_M82705-71155', 'description': '{ beds :null, beds_max :2, beds_min :1, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :650, sqft_min :650, name : 7612 S Kingston , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '8540354233', 'listing_id': '2949506207', 'prop_type': '[{type:home', 'latitude': '41.733188', 'longitude': '-87.604282', 'address': '8855 S COTTAGE GROVE AVE', 'price': 'null', 'price_max': '975', 'price_min': '975', 'link': 'https://www.realtor.com/realestateandhomes-detail/8855-S-Cott

<Response [200]>
************************************
{'property_id': '7101768831', 'listing_id': '2949505927', 'prop_type': '[{type:home', 'latitude': '41.753311', 'longitude': '-87.564185', 'address': '7800 S Essex', 'price': 'null', 'price_max': '870', 'price_min': '870', 'link': 'https://www.realtor.com/realestateandhomes-detail/7800-S-Essex-Ave_Chicago_IL_60649_M71017-68831', 'description': '{ beds :null, beds_max :3, beds_min :1, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :900, sqft_min :600, name : 7800 S Essex , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7928422694', 'listing_id': '2953713391', 'prop_type': '[{type:home', 'latitude': '41.692236', 'longitude': '-87.611897', 'address': '11111 S Vernon', 'price': 'null', 'price_max': '900', 'price_min': '900', 'link': 'https://www.realtor.com/realestateandhomes-detail/11111-S-Vernon-Ave_Chicago_IL_6062

<Response [200]>
************************************
{'property_id': '7240127829', 'listing_id': '2949505862', 'prop_type': '[{type:home', 'latitude': '41.788178', 'longitude': '-87.685461', 'address': '5800 S ARTESIAN AVE', 'price': 'null', 'price_max': '1195', 'price_min': '1195', 'link': 'https://www.realtor.com/realestateandhomes-detail/5800-S-Artesian-Ave-Apt-4_Chicago_IL_60629_M72401-27829', 'description': '{ beds :null, beds_max :3, beds_min :2, baths_min :1, baths_max :1, baths_consolidated :null, garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :897, sqft_min :708, name : 5800 W Iowa , sub_type :null, type : apartment , year_built :null'}
********************
{'property_id': '7783154884', 'listing_id': '2953713665', 'prop_type': '[{type:home', 'latitude': '41.482088', 'longitude': '-87.675665', 'address': '3324 Western Ave', 'price': 'null', 'price_max': '1400', 'price_min': '1400', 'link': 'https://www.realtor.com/realestateandhomes-detail/3324-Western-

...

<Response [200]>
************************************
{'property_id': '8946410972', 'listing_id': '2958973641', 'prop_type': '[{type:home', 'latitude': '41.916943', 'longitude': '-87.676034', 'address': '1933 N Winchester Ave Apt 2R', 'price': '2100', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-detail/1933-N-Winchester-Ave-Apt-2R_Chicago_IL_60622_M89464-10972', 'description': '{ beds :1, beds_max :null, beds_min :null, baths_min :null, baths_max :null, baths_consolidated : 1 , garage :null, garage_min :null, garage_max :null, sqft :null, sqft_max :null, sqft_min :null, name :null, sub_type : condo , type : apartment , year_built :null'}
********************
{'property_id': '9948878909', 'listing_id': '2960241159', 'prop_type': '[{type:home', 'latitude': '41.935314', 'longitude': '-87.638924', 'address': '2933 N Sheridan Rd Unit 29330804', 'price': '2095', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realest

<Response [200]>
************************************
{'property_id': '9268597644', 'listing_id': '2952530047', 'prop_type': '[{type:home', 'latitude': '41.871452', 'longitude': '-87.631287', 'address': '850 S Clark Polk St Unit 611', 'price': '2592', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-detail/850-S-Clark-St-Unit-611_Chicago_IL_60605_M92685-97644', 'description': '{ beds :1, beds_max :null, beds_min :null, baths_min :null, baths_max :null, baths_consolidated : 1 , garage :null, garage_min :null, garage_max :null, sqft :745, sqft_max :null, sqft_min :null, name :null, sub_type : condo , type : apartment , year_built :null'}
********************
{'property_id': '9071750724', 'listing_id': '2959205899', 'prop_type': '[{type:home', 'latitude': '41.978287', 'longitude': '-87.843147', 'address': '5441 N East River Rd # 21-0508', 'price': '1550', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandho

<Response [200]>
************************************
{'property_id': '9977013578', 'listing_id': '2960351749', 'prop_type': '[{type:home', 'latitude': '41.939011', 'longitude': '-87.640732', 'address': '426 W Briar Pl Unit E5', 'price': '1700', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-detail/426-W-Briar-Pl-Apt-5E_Chicago_IL_60657_M99770-13578', 'description': '{ beds :1, beds_max :null, beds_min :null, baths_min :null, baths_max :null, baths_consolidated : 1 , garage :null, garage_min :null, garage_max :null, sqft :900, sqft_max :null, sqft_min :null, name :null, sub_type : condo , type : apartment , year_built :null'}
********************
{'property_id': '9172305929', 'listing_id': '2958077585', 'prop_type': '[{type:home', 'latitude': '41.864193', 'longitude': '-87.625917', 'address': '1400 S Wabash Ave Unit 2-2', 'price': '2947', 'price_max': 'null', 'price_min': 'null', 'link': 'https://www.realtor.com/realestateandhomes-detail/1

some exception for  60
********************
page: 184
https://www.realtor.com/apartments/Chicago_IL/pg-0184


RetryError: HTTPSConnectionPool(host='api.scraperapi.com', port=443): Max retries exceeded with url: /?url=https%3A%2F%2Fwww.realtor.com%2Fapartments%2FChicago_IL%2Fpg-0184&api_key=c72673098a63fab1bc69b67253f7c93b&scraper_sdk=python (Caused by ResponseError('too many 500 error responses'))

In [4]:
df = pd.DataFrame(listings)
df

property_id  listing_id    prop_type   latitude   longitude  \
0     8229072978  2949506156  [{type:home  41.755477  -87.555892   
1     7502759759  2949506054  [{type:home  41.768031   -87.61751   
2     7929640210  2949505941  [{type:home  41.750327  -87.614027   
3     8919838642  2953713745  [{type:home  41.765835  -87.577283   
4     7012743122  2949506125  [{type:home  41.754746  -87.552012   
...          ...         ...          ...        ...         ...   
7723  9649217601  2958791947  [{type:home  41.803471  -87.584801   
7724  8775204108   617248151  [{type:home  41.870239  -87.631265   
7725  9041931653  2958053742  [{type:home  41.802731  -87.586143   
7726  8571217371  2942396256  [{type:home  41.871747   -87.63078   
7727  9271704655  2958053905  [{type:home   41.91708  -87.647591   

                             address price price_max price_min  \
0                     2817 E 77TH ST  null       870       870   
1                 6954 S CALUMET AVE  null      1110      1110   
2                  7924 S VERNON AVE  null       880       880   
3                     1931 E 71st St  null       810       810   
4              7800 S SOUTH SHORE DR  null       955       955   
...                              ...   ...       ...       ...   
7723   5035 S East End Ave Apt 2014N  2436      null      null   
7724         900 S Clark St Apt 1605  2088      null      null   
7725  1606 E Hyde Park Blvd # 01-006  1960      null      null   
7726   850 S Clark Clark St Unit 911  2424      null      null   
7727      1137 W Lawrence Ave # 1010  1945      null      null   

                                                   link  \
0     https://www.realtor.com/realestateandhomes-det...   
1     https://www.realtor.com/realestateandhomes-det...   
2     https://www.realtor.com/realestateandhomes-det...   
3     https://www.realtor.com/realestateandhomes-det...   
4     https://www.realtor.com/realestateandhomes-det...   
...                                                 ...   
7723  https://www.realtor.com/realestateandhomes-det...   
7724  https://www.realtor.com/realestateandhomes-det...   
7725  https://www.realtor.com/realestateandhomes-det...   
7726  https://www.realtor.com/realestateandhomes-det...   
7727  https://www.realtor.com/realestateandhomes-det...   

                                            description  
0     { beds :null, beds_max :4, beds_min :0, baths_...  
1     { beds :null, beds_max :3, beds_min :2, baths_...  
2     { beds :null, beds_max :1, beds_min :1, baths_...  
3     { beds :null, beds_max :1, beds_min :0, baths_...  
4     { beds :null, beds_max :1, beds_min :1, baths_...  
...                                                 ...  
7723  { beds :2, beds_max :null, beds_min :null, bat...  
7724  { beds :1, beds_max :null, beds_min :null, bat...  
7725  { beds :1, beds_max :null, beds_min :null, bat...  
7726  { beds :1, beds_max :null, beds_min :null, bat...  
7727  { beds :1, beds_max :null, beds_min :null, bat...  

[7728 rows x 11 columns]

In [5]:
#df.to_csv("Chicago_Rentals_Sample_Oct1923.csv")
df.to_csv("Chicago_Rentals_Sample_Dec2023.csv")

In [6]:
len(df.drop_duplicates())

5768

In [8]:
pages_of_results

374

In [ ]:
# drop rows that don't have a property id
prop_df = prop_df[prop_df["property_id"].notna()].reset_index(drop=True)

## Reference

In [ ]:
"""# code for working with a single page of listings

#This will give us the chunk of text with some of the listings info, to pull all the listing on a page
r3 = json_data

#get the indexes for property id and permalink so can know where to break up string for individual properties
start_idx = [idx.start() for idx in re.finditer('property_id', r3)]
end_idx = [idx.start() for idx in re.finditer('products":', r3)]

listings = []
for i in range(0, len(start_idx)-1):
    try:

        #loop through the text of html on a page and pull out the slices that correspond to a particular property.
        # don't use the end index, it throws everything off. Also search will just find the first match so it's fine.
        # search returns a match object
        r4 = r3[start_idx[i] : ]#end_idx[i]]

        listing_id = re.search('listing_id":(.+?),', r4)
        property_id = re.search('property_id":(.+?),', r4)
        prop_type = re.search('prop_type":(.+?),', r4)
        lat= re.search('lat":(.+?),', r4)    
        lon = re.search('lon":(.+?)}', r4)    
        address = re.search('line":(.+?),', r4)
        price = re.search('list_price":(.+?),', r4)
        price_max = re.search('list_price_max":(.+?),', r4)
        price_min = re.search('list_price_min":(.+?),', r4)
        permalink = re.search('permalink":(.+?),', r4)
        description = re.search('"description":(.*?)}', r4)
        """
        print(listing_id)
        print(address)
        print(price_max)
        print(permalink)
        print(description)
        """
        
        # create a list of dictionaries to store the info
        
        dic = {'property_id': property_id.group(1).replace('"',''),
                'listing_id' : listing_id.group(1).replace('"',''), 
                'prop_type' : prop_type.group(1).replace('"',''), 
                'latitude': lat.group(1), 
                'longitude': lon.group(1), 
                'address': address.group(1).replace('"',''),
                'price': price.group(1).replace('"',''),
                'price_max' : price_max.group(1).replace('"',''),
                'price_min' : price_max.group(1).replace('"',''),
                'link' : 'https://www.realtor.com/realestateandhomes-detail/' + permalink.group(1).replace('"',''),
                'description' : description.group(1).replace('"',' '),
               }
        print(dic)
        print("********************")
        listings.append(dic)
        
    except:
        print("some exception for ", i)
        print("********************")
        """